In [1]:
import pandas as pd
import numpy as np
import random
from numpy.random import RandomState
from scipy import stats
from scipy.optimize import minimize
import scipy
import os
os.environ['R_HOME'] = '/Library/Frameworks/R.framework/Versions/4.1/Resources/'
import rpy2
from rpy2.robjects.packages import importr
from rpy2.robjects.packages import SignatureTranslatedAnonymousPackage
import datetime
from rpy2.robjects.vectors import FloatVector
from statsmodels.tsa.stattools import adfuller
from sklearn.linear_model import LinearRegression

real_data_folder = "/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_mixed_period_2000_2021/"
np.random.seed(881)


# Define the model that generates pair simulations.
yuima = importr("yuima")
n_jumpou_NIG_sim_string = """
n_jumpou_NIG = function(random_seed, num_sim,
                        mu11, mu12, mu21, mu22, 
                        sigma11, sigma12, sigma21, sigma22,
                        j11, j12, j21, j22,
                        alpha, beta1, beta2, delta0, mu1, mu2, 
                        lambda11, lambda12, lambda21, lambda22,
                        xinit_vec, T0, T, length){
  
  set.seed(random_seed)
  
  drift = c("mu11*t-mu12*X1", "mu21*t-mu22*X2")
  diffusion = matrix(c("exp(sigma11)", "exp(sigma12)", "exp(sigma21)", "exp(sigma22)"), 2, 2, byrow=TRUE)
  jumpcoef = matrix(c("j11", "j12", "j21", "j22"), 2, 2, byrow=TRUE) 
  
  alpha = alpha
  beta = c(beta1, beta2)
  delta0 = delta0
  mu = c(mu1, mu2)
  Lambda = matrix(c(lambda11, lambda12, lambda21, lambda22), 2, 2, byrow=TRUE)
  
  ou_model = setModel(drift=drift, diffusion=diffusion, jump.coeff=jumpcoef, 
                      measure.type="code",
                      measure=list(df="rNIG(z, alpha, beta, delta0, mu, Lambda)"), 
                      time.variable = "t",
                      state.var=c("X1","X2"), solve.variable=c("X1","X2"))
  newsamp = setSampling(Initial=T0, Terminal=T, n=length)
  
  n_sim_data = data.frame(matrix(nrow=length+1, ncol=2*num_sim))
  for (i in 1:num_sim){
    jumpou_sim = simulate(ou_model, 
                          true.par=list(
                            mu11=mu11, mu12=mu12, mu21=mu21, mu22=mu22, 
                            sigma11=sigma11, sigma12=sigma12, sigma21=sigma21, sigma22=sigma22,
                            j11=j11, j12=j12, j21=j21, j22=j22,
                            alpha=alpha, beta=beta, delta0=delta0, mu=mu, Lambda=Lambda), 
                          xinit=xinit_vec[[i]], sampling=newsamp)
    original_data = jumpou_sim@data@original.data
    one_sim_jumpou = data.frame(original_data[,1], original_data[,2])
    colnames(one_sim_jumpou) = c('series1', 'series2')
    n_sim_data[, (2*i-1):(2*i)] = one_sim_jumpou
  }
  return(n_sim_data)
}
"""

n_jumpou_NIG_sim = SignatureTranslatedAnonymousPackage(n_jumpou_NIG_sim_string, "n_jumpou_NIG_sim")
def n_jumpou_simulation(random_seed, num_sim,
                        mu11, mu12, mu21, mu22, 
                        sigma11, sigma12, sigma21, sigma22,
                        j11, j12, j21, j22,
                        alpha, beta1, beta2, delta0, mu1, mu2, 
                        lambda11, lambda12, lambda21, lambda22,
                        xinit_vec, T0, T, length):

    n_sim_data = pd.DataFrame(
        n_jumpou_NIG_sim.n_jumpou_NIG(random_seed, num_sim,
                                      mu11, mu12, mu21, mu22, 
                                      sigma11, sigma12, sigma21, sigma22,
                                      j11, j12, j21, j22,
                                      alpha, beta1, beta2, delta0, mu1, mu2, 
                                      lambda11, lambda12, lambda21, lambda22,
                                      xinit_vec, T0, T, length)).transpose()
    return n_sim_data


def price_to_log_price(n_price):
    return(np.log(n_price))

def log_price_to_price(n_log_price):
    return(np.exp(n_log_price))

def price_to_return(n_price):
    n_return = pd.DataFrame()
    for i in range(n_price.shape[1]):
        ith_column_price_series = n_price.iloc[:, i]
        n_return = pd.concat([n_return, 100 * (np.log(ith_column_price_series[1:].values) - np.log(ith_column_price_series[:-1]))], axis=1)
    return n_return

def log_price_to_return(n_log_price):
    n_real_return = pd.DataFrame()
    for i in range(n_log_price.shape[1]):
        ith_column_price_series = n_log_price.iloc[:, i]
        n_real_return = pd.concat([n_real_return, 100 * (ith_column_price_series[1:].values - ith_column_price_series[:-1])], axis=1)
    return n_real_return


def cross_corr_coef(lag_time_series, lead_time_series, lag):
    # calculate the cross correlation between two time series
    # if the result is not zero, then 'lead_time_series' leads 'lag_time_series'
    lag_time_series = lag_time_series.iloc[lag:]
    corr_coef = np.corrcoef(lag_time_series, lead_time_series.iloc[0:((lead_time_series.size)-lag)])[0][1]
    return corr_coef


def cal_stats(n_return, n_price):
    
    return_series1 = n_return.iloc[:, ::2]
    return_series2 = n_return.iloc[:, 1::2]
    price_series1 = n_price.iloc[:, ::2]
    price_series2 = n_price.iloc[:, 1::2]
    sq_return_series1 = return_series1**2
    sq_return_series2 = return_series2**2

    
    mean1 = return_series1.mean(axis=0).values
    sd1 = return_series1.std(axis=0).values
    skew1 = return_series1.skew(axis=0).values
    kurtosis1 = return_series1.kurtosis(axis=0).values
       
    
    mean2 = return_series2.mean(axis=0).values
    sd2 = return_series2.std(axis=0).values
    skew2 = return_series2.skew(axis=0).values
    kurtosis2 = return_series2.kurtosis(axis=0).values #8(8)
    
    
    
    # Autocorrelation of the 2 return series with 3 lags respectively
    autocorr1_lag_1 = return_series1.apply(lambda x: x.autocorr(lag=1))
    autocorr1_lag_2 = return_series1.apply(lambda x: x.autocorr(lag=2))
    autocorr1_lag_3 = return_series1.apply(lambda x: x.autocorr(lag=3))
    autocorr2_lag_1 = return_series2.apply(lambda x: x.autocorr(lag=1)) 
    autocorr2_lag_2 = return_series2.apply(lambda x: x.autocorr(lag=2)) 
    autocorr2_lag_3 = return_series2.apply(lambda x: x.autocorr(lag=3)) #6(14)
    
    # Cross-correlation between return series
    corr_ts1_lag_0 = []
    corr_ts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_ts1_lag_2 = []
    corr_ts1_lag_3 = []
    corr_ts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_ts2_lag_2 = []
    corr_ts2_lag_3 = []
    for i in range(int(real_price.shape[1]/2)):
        corr_ts1_lag_0.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 0))
        corr_ts1_lag_1.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 1))
        corr_ts1_lag_2.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 2))
        corr_ts1_lag_3.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 3))
        corr_ts2_lag_1.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 1))
        corr_ts2_lag_2.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 2))
        corr_ts2_lag_3.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 3))
    corr_ts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_ts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_ts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_ts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_ts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_ts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_ts2_lag_3 = pd.Series(corr_ts2_lag_3)#7(21)
    
    
    
    # Autocorrelation of the 2 squared returns with 3 lags respectively
    autocorr_sqreturn_1_lag_1 = sq_return_series1.apply(lambda x: x.autocorr(lag=1))
    autocorr_sqreturn_1_lag_2 = sq_return_series1.apply(lambda x: x.autocorr(lag=2))
    autocorr_sqreturn_1_lag_3 = sq_return_series1.apply(lambda x: x.autocorr(lag=3))
    autocorr_sqreturn_2_lag_1 = sq_return_series2.apply(lambda x: x.autocorr(lag=1)) 
    autocorr_sqreturn_2_lag_2 = sq_return_series2.apply(lambda x: x.autocorr(lag=2)) 
    autocorr_sqreturn_2_lag_3 = sq_return_series2.apply(lambda x: x.autocorr(lag=3))#6(27)
    
    # Cross-correlation between squared returns series
    corr_sqts1_lag_0 = []
    corr_sqts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_sqts1_lag_2 = []
    corr_sqts1_lag_3 = []
    corr_sqts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_sqts2_lag_2 = []
    corr_sqts2_lag_3 = []
    for i in range(int(real_price.shape[1]/2)):
        corr_sqts1_lag_0.append(cross_corr_coef(sq_return_series1.iloc[:, i], sq_return_series2.iloc[:, i], 0))
        corr_sqts1_lag_1.append(cross_corr_coef(sq_return_series1.iloc[:, i], sq_return_series2.iloc[:, i], 1))
        corr_sqts1_lag_2.append(cross_corr_coef(sq_return_series1.iloc[:, i], sq_return_series2.iloc[:, i], 2))
        corr_sqts1_lag_3.append(cross_corr_coef(sq_return_series1.iloc[:, i], sq_return_series2.iloc[:, i], 3))
        corr_sqts2_lag_1.append(cross_corr_coef(sq_return_series2.iloc[:, i], sq_return_series1.iloc[:, i], 1))
        corr_sqts2_lag_2.append(cross_corr_coef(sq_return_series2.iloc[:, i], sq_return_series1.iloc[:, i], 2))
        corr_sqts2_lag_3.append(cross_corr_coef(sq_return_series2.iloc[:, i], sq_return_series1.iloc[:, i], 3))
    corr_sqts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_sqts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_sqts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_sqts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_sqts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_sqts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_sqts2_lag_3 = pd.Series(corr_ts2_lag_3)#7(34)
    
    
    
    
    stats_data = pd.DataFrame([mean1, mean2, sd1, sd2, 
                               skew1, skew2, kurtosis1, kurtosis2, #8(8)
                               
                               autocorr1_lag_1, autocorr1_lag_2, autocorr1_lag_3,
                               autocorr2_lag_1, autocorr2_lag_2, autocorr2_lag_3,#6(14)
                               
                               corr_ts1_lag_0, 
                               corr_ts1_lag_1, corr_ts1_lag_2, corr_ts1_lag_3,
                               corr_ts2_lag_1, corr_ts2_lag_2, corr_ts2_lag_3, #7(21)
                               
                               autocorr_sqreturn_1_lag_1, autocorr_sqreturn_1_lag_2, autocorr_sqreturn_1_lag_3,
                               autocorr_sqreturn_2_lag_1, autocorr_sqreturn_2_lag_2, autocorr_sqreturn_2_lag_3,#6(27)
                               
                               corr_sqts1_lag_0,
                               corr_sqts1_lag_1, corr_sqts1_lag_2, corr_sqts1_lag_3,
                               corr_sqts2_lag_1, corr_sqts2_lag_2, corr_sqts2_lag_3])#7(34)
    stats_data = stats_data.transpose()
    stats_data.columns = [
        'return_mean1', 'return_mean2',
        'return_sd1', 'return_sd2',
        'return_skew1', 'return_skew2',
        'return_kurtosis1', 'return_kurtosis2',
        
        'return_autocorrelation_ts1_lag1', 'return_autocorrelation_ts1_lag2', 'return_autocorrelation_ts1_lag3',
        'return_autocorrelation_ts2_lag1', 'return_autocorrelation_ts2_lag2', 'return_autocorrelation_ts2_lag3',
        
        'return_correlation_ts1_lag_0',
        'return_correlation_ts1_lag_1', 'return_correlation_ts1_lag_2', 'return_correlation_ts1_lag_3',
        'return_correlation_ts2_lag_1', 'return_correlation_ts2_lag_2', 'return_correlation_ts2_lag_3',
        
        'sqreturn_autocorrelation_ts1_lag1', 'sqreturn_autocorrelation_ts1_lag2', 'sqreturn_autocorrelation_ts1_lag3',
        'sqreturn_autocorrelation_ts2_lag1', 'sqreturn_autocorrelation_ts2_lag2', 'sqreturn_autocorrelation_ts2_lag3',
    
        'sqreturn_correlation_ts1_lag_0',
        'sqreturn_correlation_ts1_lag_1', 'sqreturn_correlation_ts1_lag_2', 'sqreturn_correlation_ts1_lag_3', 
        'sqreturn_correlation_ts2_lag_1', 'sqreturn_correlation_ts2_lag_2', 'sqreturn_correlation_ts2_lag_3']
    
    return stats_data


def loss_function(params):

    params = FloatVector(params)
    print(params)
    moment_loss = pd.DataFrame().reindex_like(real_stats)

    n_real_log_price = n_jumpou_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=mu11, mu12=mu12, 
        mu21=mu21, mu22=mu22, 
        sigma11=sigma11, sigma12=sigma12, 
        sigma21=sigma21, sigma22=sigma22,
        j11=j11, j12=j12, 
        j21=j21, j22=j22,
        alpha=alpha, 
        beta1=beta1, beta2=beta2,
        delta0=delta0, 
        mu1=mu1, mu2=mu2, 
        lambda11=lambda11, lambda12=lambda12, 
        lambda21=lambda21, lambda22=1/lambda11, 
        xinit_vec=xinit_vec, T0=T0, T=T, length=length)
    n_real_price = log_price_to_price(n_real_log_price)
    n_real_return = price_to_return(n_real_price)
    n_real_stats = cal_stats(n_real_return, n_real_price)
    
    
    n_sim_log_price = n_jumpou_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=params[0], mu12=params[1], 
        mu21=params[2], mu22=params[3], 
        sigma11=params[4], sigma12=params[5], 
        sigma21=params[6], sigma22=params[7],
        j11=params[8], j12=params[9], 
        j21=params[10], j22=params[11],
        alpha=params[12], 
        beta1=beta1, beta2=beta2, 
        delta0=params[13], 
        mu1=params[14], mu2=params[15], 
        lambda11=params[16], lambda12=lambda12, 
        lambda21=lambda21, lambda22=1/params[16],
        xinit_vec=xinit_vec, T0=T0, T=T, length=length)
    n_sim_price = log_price_to_price(n_sim_log_price)
    n_sim_return = price_to_return(n_sim_price)
    n_sim_stats = cal_stats(n_sim_return, n_sim_price)


    moment_loss = np.abs(n_real_stats - n_sim_stats)
    sum_loss = np.sum(moment_loss)
    
    sum_loss[6] = sum_loss[6]/10 
    sum_loss[7] = sum_loss[7]/10 
    
    loss = np.sum(sum_loss)
    
    print(sum_loss)
    print(loss)
    print('----------')

    return loss


mu11, mu12, mu21, mu22 = 1.106313229, 0.137674347, 1.409624594, 0.229410620
sigma11, sigma12, sigma21, sigma22 = -2.480359850, -1.314594072, -1.320184879, -5.084637560
j11, j12, j21, j22 = -0.006039563, -0.091907975, -0.039125514, -0.070469278
alpha, delta0, mu1, mu2, lambda11 = 2.547227215, 4.794909585, 9.866465848, 3.126667339, 2.013943232

beta1 = 0
beta2 = 0
lambda12 = 0
lambda21 = 0


real_price = pd.read_csv(real_data_folder + "pair_prices_cal.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv(real_data_folder + "pair_returns_cal.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)


xinit_vec = []
for i in range(int(real_log_price.shape[1]/2)):
    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
num_sim, T0, T, length = real_stats.shape[0], 0, 2, real_price.shape[0]


initial0 = [1, 1, 1, 1,
            -1, -1, -1, -1,
            0.1, 0.1, 0.1, 0.1,
            1, 1,
            1, 1,
            1]
begin_time = datetime.datetime.now()
res = minimize(loss_function, initial0, method='Powell',
               tol=1e-6, options={'disp': True},
               bounds=[(0, None), (0, None), (0, None), (0, None),
                       (None, None), (None, None), (None, None), (None, None),
                       (None, None), (None, None), (None, None), (None, None),
                       (0, None), (0, None),
                       (None, None), (None, None), 
                       (0, None)])
print(res.x)

time = datetime.datetime.now() - begin_time
print(time)

params = (res.x)
loss = loss_function((params))
print(loss)

 [1]  1.0  1.0  1.0  1.0 -1.0 -1.0 -1.0 -1.0  0.1  0.1  0.1  0.1  1.0  1.0  1.0
[16]  1.0  1.0

return_mean1                         110.482051
return_mean2                          89.503662
return_sd1                           383.386582
return_sd2                           395.087547
return_skew1                          70.607711
return_skew2                          81.214842
return_kurtosis1                      38.725800
return_kurtosis2                      46.265782
return_autocorrelation_ts1_lag1       13.189607
return_autocorrelation_ts1_lag2       11.772338
return_autocorrelation_ts1_lag3       12.319339
return_autocorrelation_ts2_lag1       13.056153
return_autocorrelation_ts2_lag2       11.876449
return_autocorrelation_ts2_lag3       13.671531
return_correlation_ts1_lag_0         153.161074
return_correlation_ts1_lag_1          12.811166
return_correlation_ts1_lag_2          12.155189
return_correlation_ts1_lag_3          12.334393
return_correlation_ts2_lag_1          12

return_mean1                          29.888367
return_mean2                          88.050002
return_sd1                           389.697782
return_sd2                           394.685735
return_skew1                          84.524655
return_skew2                          95.153222
return_kurtosis1                      51.117455
return_kurtosis2                      57.012375
return_autocorrelation_ts1_lag1       13.291372
return_autocorrelation_ts1_lag2       12.532115
return_autocorrelation_ts1_lag3       13.170525
return_autocorrelation_ts2_lag1       12.690688
return_autocorrelation_ts2_lag2       13.778247
return_autocorrelation_ts2_lag3       13.290583
return_correlation_ts1_lag_0         152.529308
return_correlation_ts1_lag_1          12.879427
return_correlation_ts1_lag_2          12.979639
return_correlation_ts1_lag_3          13.554855
return_correlation_ts2_lag_1          11.898431
return_correlation_ts2_lag_2          12.382623
return_correlation_ts2_lag_3          11

return_mean1                          30.754366
return_mean2                          87.890329
return_sd1                           392.873848
return_sd2                           394.580673
return_skew1                          77.727412
return_skew2                          84.470639
return_kurtosis1                      47.487619
return_kurtosis2                      51.823199
return_autocorrelation_ts1_lag1       12.545088
return_autocorrelation_ts1_lag2       12.639131
return_autocorrelation_ts1_lag3       14.275167
return_autocorrelation_ts2_lag1       13.269542
return_autocorrelation_ts2_lag2       14.466426
return_autocorrelation_ts2_lag3       13.923463
return_correlation_ts1_lag_0         153.015418
return_correlation_ts1_lag_1          12.386758
return_correlation_ts1_lag_2          12.377348
return_correlation_ts1_lag_3          14.081244
return_correlation_ts2_lag_1          12.502013
return_correlation_ts2_lag_2          12.333929
return_correlation_ts2_lag_3          12

return_mean1                          30.956672
return_mean2                          85.705645
return_sd1                           389.946498
return_sd2                           393.162667
return_skew1                          63.098875
return_skew2                          69.364115
return_kurtosis1                      30.384520
return_kurtosis2                      33.268685
return_autocorrelation_ts1_lag1       13.413175
return_autocorrelation_ts1_lag2       12.450910
return_autocorrelation_ts1_lag3       13.185267
return_autocorrelation_ts2_lag1       12.501833
return_autocorrelation_ts2_lag2       12.664264
return_autocorrelation_ts2_lag3       13.795932
return_correlation_ts1_lag_0         153.971280
return_correlation_ts1_lag_1          12.663962
return_correlation_ts1_lag_2          12.313119
return_correlation_ts1_lag_3          12.717898
return_correlation_ts2_lag_1          12.734069
return_correlation_ts2_lag_2          12.664062
return_correlation_ts2_lag_3          13

return_mean1                          29.267473
return_mean2                          90.394316
return_sd1                           393.195094
return_sd2                           398.282025
return_skew1                          78.974701
return_skew2                          90.395289
return_kurtosis1                      55.965050
return_kurtosis2                      61.120246
return_autocorrelation_ts1_lag1       13.340852
return_autocorrelation_ts1_lag2       13.810507
return_autocorrelation_ts1_lag3       11.367783
return_autocorrelation_ts2_lag1       12.718551
return_autocorrelation_ts2_lag2       12.658972
return_autocorrelation_ts2_lag3       12.154848
return_correlation_ts1_lag_0         153.701040
return_correlation_ts1_lag_1          12.855209
return_correlation_ts1_lag_2          13.466897
return_correlation_ts1_lag_3          11.216778
return_correlation_ts2_lag_1          12.355898
return_correlation_ts2_lag_2          12.492658
return_correlation_ts2_lag_3          12

...

return_mean1                         20.856702
return_mean2                         18.735220
return_sd1                           19.587244
return_sd2                           24.587935
return_skew1                         37.748171
return_skew2                         54.982758
return_kurtosis1                     11.223750
return_kurtosis2                     22.723001
return_autocorrelation_ts1_lag1      12.877618
return_autocorrelation_ts1_lag2      13.025432
return_autocorrelation_ts1_lag3      12.433991
return_autocorrelation_ts2_lag1      13.894359
return_autocorrelation_ts2_lag2      13.744985
return_autocorrelation_ts2_lag3      11.874048
return_correlation_ts1_lag_0         10.647842
return_correlation_ts1_lag_1         12.661574
return_correlation_ts1_lag_2         12.897654
return_correlation_ts1_lag_3         12.551182
return_correlation_ts2_lag_1         12.898734
return_correlation_ts2_lag_2         13.263719
return_correlation_ts2_lag_3         12.794463
sqreturn_auto

return_mean1                         20.832357
return_mean2                         19.408563
return_sd1                           20.775295
return_sd2                           24.172359
return_skew1                         42.454546
return_skew2                         56.446344
return_kurtosis1                     15.216833
return_kurtosis2                     24.178704
return_autocorrelation_ts1_lag1      11.731627
return_autocorrelation_ts1_lag2      13.522761
return_autocorrelation_ts1_lag3      13.229405
return_autocorrelation_ts2_lag1      13.318599
return_autocorrelation_ts2_lag2      14.004981
return_autocorrelation_ts2_lag3      13.197068
return_correlation_ts1_lag_0         12.159886
return_correlation_ts1_lag_1         12.868581
return_correlation_ts1_lag_2         13.171127
return_correlation_ts1_lag_3         14.214413
return_correlation_ts2_lag_1         12.671195
return_correlation_ts2_lag_2         12.854212
return_correlation_ts2_lag_3         12.299586
sqreturn_auto

return_mean1                         18.889018
return_mean2                         19.361727
return_sd1                           20.188467
return_sd2                           23.168934
return_skew1                         41.597511
return_skew2                         58.110625
return_kurtosis1                     16.486350
return_kurtosis2                     25.266503
return_autocorrelation_ts1_lag1      12.872060
return_autocorrelation_ts1_lag2      13.052258
return_autocorrelation_ts1_lag3      13.118038
return_autocorrelation_ts2_lag1      13.106514
return_autocorrelation_ts2_lag2      12.524298
return_autocorrelation_ts2_lag3      12.786499
return_correlation_ts1_lag_0         12.117929
return_correlation_ts1_lag_1         12.723378
return_correlation_ts1_lag_2         14.201238
return_correlation_ts1_lag_3         13.573226
return_correlation_ts2_lag_1         12.750296
return_correlation_ts2_lag_2         13.413937
return_correlation_ts2_lag_3         12.335199
sqreturn_auto

return_mean1                         21.333140
return_mean2                         21.042847
return_sd1                           19.581852
return_sd2                           23.116676
return_skew1                         42.324546
return_skew2                         56.782546
return_kurtosis1                     14.253398
return_kurtosis2                     22.985899
return_autocorrelation_ts1_lag1      12.999933
return_autocorrelation_ts1_lag2      12.808118
return_autocorrelation_ts1_lag3      12.770375
return_autocorrelation_ts2_lag1      12.765062
return_autocorrelation_ts2_lag2      12.760881
return_autocorrelation_ts2_lag3      14.782221
return_correlation_ts1_lag_0         12.358165
return_correlation_ts1_lag_1         12.708932
return_correlation_ts1_lag_2         12.386021
return_correlation_ts1_lag_3         12.523354
return_correlation_ts2_lag_1         12.659491
return_correlation_ts2_lag_2         12.638550
return_correlation_ts2_lag_3         13.577034
sqreturn_auto

return_mean1                         19.746018
return_mean2                         21.583096
return_sd1                           19.708709
return_sd2                           26.084751
return_skew1                         47.355548
return_skew2                         60.761598
return_kurtosis1                     16.142119
return_kurtosis2                     29.699930
return_autocorrelation_ts1_lag1      12.871677
return_autocorrelation_ts1_lag2      12.952227
return_autocorrelation_ts1_lag3      13.443436
return_autocorrelation_ts2_lag1      12.935196
return_autocorrelation_ts2_lag2      13.730036
return_autocorrelation_ts2_lag3      13.010798
return_correlation_ts1_lag_0         11.583455
return_correlation_ts1_lag_1         12.341790
return_correlation_ts1_lag_2         13.170711
return_correlation_ts1_lag_3         11.546059
return_correlation_ts2_lag_1         13.652220
return_correlation_ts2_lag_2         13.431404
return_correlation_ts2_lag_3         12.784087
sqreturn_auto

In [2]:
mu11, mu12, mu21, mu22 = 1.106313229, 0.137674347, 1.409624594, 0.229410620
sigma11, sigma12, sigma21, sigma22 = -2.480359850, -1.314594072, -1.320184879, -5.084637560
j11, j12, j21, j22 = -0.006039563, -0.091907975, -0.039125514, -0.070469278
alpha, beta, delta0, mu, Lambda = 2.547227215, 4.794909585, 9.866465848, 3.126667339, 2.013943232

print(params)

[ 1.39272907  0.30684845  1.78569683  0.53778256 -2.40880162 -1.31427205
 -1.34325143 -3.91481024  0.00633029 -0.09420594 -0.03869046  0.04329196
  3.35755037  2.67105643  3.36184182  1.75948642  4.28635868]
